In [25]:
using Plots
plotly()

Plots.PlotlyBackend()

In [26]:
    mm = 1 #parâmetro gama de aprendizagem, quanto mais alto mais precisa a escolha da regra
    pstar = 0 #meta de inflação
    eprational=0 #igual a 1 se todos forem racionais para a inflação
    epextrapol=0 #igual a 1 se todos forem extrapoladores para a inflação
    
    a1 = 0.5 #coeficiente do produto esperado no produto
    a2 = -0.2 #sensibilidade a juros do produto
    
    b1 = 0.5 #coeficiente da inflação esperada na inflação
    b2 = 0.05 #coeficiente do produto na inflação
    
    c1 = 1.5 #coeficiente da inflação na regra de Taylor
    c2 = 0.5 #coeficiente do produto na regra de Taylor
    c3 = 0.5 #coeficiente auto-regressivo na regra de Taylor
    
    A = [1 -b2;-a2*c1 1-a2*c2]
    B = [b1 0;-a2 a1]
    C = [1-b1 0;0 1-a1]
    T = 200 #número de períodos
    TI = 250
    K = 50

    sigma1 = 0.5 #desvio-padrão dos choques no produto
    sigma2 = 0.5 #desvio-padrão dos choques na inflação
    sigma3 = 0.5 #desvio-padrão dos choques nos juros

    rhoout=0.0 #coeficiente auto-regressivo do choque no produto
    rhoinf=0.0 #coeficiente auto-regressivo do choque na inflação
    rhotayl=0.0 #coeficiente auto-regressivo do choque na regra de Taylor

    rho=0.5 #coeficiente auto-regressivo do EQM
    rhoBH=0.0 #coeficiente auto-regressivo da regra escolhida

    epfs=pstar
    p = zeros(T)
    y = zeros(T)
    plagt = zeros(T)
    ylagt = zeros(T)
    r = zeros(T)
    epf = zeros(T)
    epc = zeros(T)
    ep = zeros(T)
    ey = zeros(T)
    CRp = zeros(T)
    FRp = zeros(T)
    alfapt = zeros(T)
    eyfunt = zeros(T)
    CRy = zeros(T)
    FRy = zeros(T)
    alfayt = zeros(T)
    anspirits = zeros(T)
    epsilont = zeros(T)
    etat = zeros(T)
    ut = zeros(T)
    eps1 = zeros(T)

    alfap=0.5 #proporção inicial de extrapoladores de inflação
    alfay=0.5 #proporção inicial de extrapoladores do produto
    K1=K+1

    for t in 2:200
      epsilont[t] = rhoout*epsilont[t-1] + sigma1*randn()
      etat[t]= rhoinf*etat[t-1] + sigma2*randn()
      ut[t] = rhotayl*ut[t-1] + sigma3*randn()
      epsilon = epsilont[t]
      eta = etat[t]
      u = ut[t]
      shocks = [eta;a2*u+epsilon]
      epcs = p[t-1]
      if eprational==1
        epcs=pstar
      end
      eps1=alfap*epcs+(1-alfap)*epfs
      if epextrapol==1
        eps1=p[t-1]
      end
      eychar=y[t-1]
      eyfun=0  +randn()/2
      eyfunt[t]=eyfun
      eys=alfay*eychar+(1-alfay)*eyfun
      forecast = [eps1;eys]
      plag=p[t-1]
      ylag=y[t-1]
      rlag=r[t-1]
      lag = [plag;ylag]
      smooth = [0;a2*c3]
      D = B*forecast + C*lag + smooth*rlag + shocks
      X = A\D
      p[t]= X[1,1]
      y[t]= X[2,1]
      r[t]= c1*p[t]+c2*y[t]+c3*r[t-1]+u
      plagt[t]=p[t-1]
      ylagt[t]=y[t-1]
      CRp[t] = rho*CRp[t-1] - (1-rho)*(epcs-p[t])^2
      FRp[t] = rho*FRp[t-1] - (1-rho)*(epfs-p[t])^2
      CRy[t] = rho*CRy[t-1] - (1-rho)*(eychar-y[t])^2
      FRy[t] = rho*FRy[t-1] - (1-rho)*(eyfun-y[t])^2
      alfap = rhoBH*alfapt[t-1]+(1-rhoBH)*exp(mm*CRp[t])/(exp(mm * CRp[t]) + exp(mm * FRp[t]))
      alfay = rhoBH*alfayt[t-1]+(1-rhoBH)*exp(mm*CRy[t])/(exp(mm * CRy[t]) + exp(mm * FRy[t]))
      alfapt[t] = alfap
      alfayt[t] = alfay
      if eychar>0
        anspirits[t]=alfay
      end
      if eychar<0
        anspirits[t]=1-alfay
      end
    end


In [27]:

plot(y, label="y");
plot!(anspirits, label="animal spirits")

<!DOCTYPE html>
 
 
 Plots.jl

In [10]:
plot(p, label="p");
plot!(r, label="r")

<!DOCTYPE html>
 
 
 Plots.jl

In [11]:
histogram(y)

<!DOCTYPE html>
 
 
 Plots.jl

In [12]:
using HypothesisTests
JarqueBeraTest(y)

Jarque-Bera normality test
--------------------------
Population details:
    parameter of interest:   skewness and kurtosis
    value under h_0:         "0 and 3"
    point estimate:          "-0.09841350190297563 and 2.8307576011399567"

Test summary:
    outcome with 95% confidence: fail to reject h_0
    one-sided p-value:           0.7552

Details:
    number of observations:         200
    JB statistic:                   0.5615321583260828


In [16]:
using Statistics
cor(y, anspirits)

0.7555656385829329

In [17]:
#Função impulso-resposta

T = 50 #número de períodos

M=Array{Float64,2}(undef, T, 100) #Matriz que armazena o impulso resposta de todas as simulações
L=Array{Float64,2}(undef, T, 2) #Matriz que armazena a série com e sem choque em cada simulação


for i in 1:100 #número de simulações
    

    
    epsilont = zeros(T, 2) #choques no produto
    etat = zeros(T, 2) #choques na inflação
    ut = zeros(T, 2) #choques nos juros
    
    sigma1 = 0.5 #desvio-padrão dos choques no produto
    sigma2 = 0.5 #desvio-padrão dos choques na inflação
    sigma3 = 0.5 #desvio-padrão dos choques nos juros
    
#############################################Escolhe qual variável recebe o choque##########################################
    
    epsilont[2,2] = sigma1
    #etat[2,2]= sigma2
    #ut[2,2] = sigma3
    
#############################################################################################################################
    
    mm = 1 #parâmetro gama de aprendizagem, quanto mais alto mais precisa a escolha da regra
    pstar = 0 #meta de inflação
    eprational=0 #igual a 1 se todos forem racionais para a inflação
    epextrapol=0 #igual a 1 se todos forem extrapoladores para a inflação
    
    a1 = 0.5 #coeficiente do produto esperado no produto
    a2 = -0.2 #sensibilidade a juros do produto
    
    b1 = 0.5 #coeficiente da inflação esperada na inflação
    b2 = 0.05 #coeficiente do produto na inflação
    
    c1 = 1.5 #coeficiente da inflação na regra de Taylor
    c2 = 0.5 #coeficiente do produto na regra de Taylor
    c3 = 0.5 #coeficiente auto-regressivo na regra de Taylor
    
    A = [1 -b2;-a2*c1 1-a2*c2]
    B = [b1 0;-a2 a1]
    C = [1-b1 0;0 1-a1]

    TI = 250
    K = 50
    

    rho=0.5 #coeficiente auto-regressivo do EQM

    rhoBH=0.0 #coeficiente auto-regressivo da regra escolhida
    
    epfs=pstar #previsão de inflação dos agentes racionais
    eps1 = zeros(T)
    p = zeros(T)
    y = zeros(T)
    plagt = zeros(T)
    ylagt = zeros(T)
    r = zeros(T)
    epf = zeros(T)
    epc = zeros(T)
    ep = zeros(T)
    ey = zeros(T)
    CRp = zeros(T)
    FRp = zeros(T)
    alfapt = zeros(T)
    eyfunt = zeros(T)
    CRy = zeros(T)
    FRy = zeros(T)
    alfayt = zeros(T)
    anspirits = zeros(T)

    alfap=0.5 #proporção inicial de extrapoladores de inflação
    alfay=0.5 #proporção inicial de extrapoladores do produto
    
    K1=K+1
    

    for j in 1:2 #primeira vez sem choque, segunda com choque
        for t in 2:T

          epsilon = epsilont[t, j] #COLOCAR O j SÓ NA VARIÁVEL QUE RECEBE O CHOQUE
          eta = etat[t]
          u = ut[t]
          
          shocks = [eta;a2*u+epsilon]
          epcs = p[t-1]
          if eprational==1
            epcs=pstar
          end
          eps1=alfap*epcs+(1-alfap)*epfs
          if epextrapol==1
            eps1=p[t-1]
          end
          eychar=y[t-1]
          eyfun=0 #+ randn()/2 
          eyfunt[t]=eyfun
          eys=alfay*eychar+(1-alfay)*eyfun
          forecast = [eps1;eys]
          plag=p[t-1]
          ylag=y[t-1]
          rlag=r[t-1]
          lag = [plag;ylag]
          smooth = [0;a2*c3]
          D = B*forecast + C*lag + smooth*rlag + shocks
          X = A\D
          p[t]= X[1,1]
          y[t]= X[2,1]
          r[t]= c1*p[t]+c2*y[t]+c3*r[t-1]+u
          plagt[t]=p[t-1]
          ylagt[t]=y[t-1]
          CRp[t] = rho*CRp[t-1] - (1-rho)*(epcs-p[t])^2
          FRp[t] = rho*FRp[t-1] - (1-rho)*(epfs-p[t])^2
          CRy[t] = rho*CRy[t-1] - (1-rho)*(eychar-y[t])^2
          FRy[t] = rho*FRy[t-1] - (1-rho)*(eyfun-y[t])^2
          alfap = rhoBH*alfapt[t-1]+(1-rhoBH)*exp(mm*CRp[t])/(exp(mm * CRp[t]) + exp(mm * FRp[t]))
          alfay = rhoBH*alfayt[t-1]+(1-rhoBH)*exp(mm*CRy[t])/(exp(mm * CRy[t]) + exp(mm * FRy[t]))
          alfapt[t] = alfap
          alfayt[t] = alfay
          if eychar>0
            anspirits[t]=alfay
          end
          if eychar<0
            anspirits[t]=1-alfay
          end
        end
        L[:,j]=y[:,1] #Armazena a variável que recebe o choque
    end
    M[:,i]=L[:,2]-L[:,1] #Armazena a diferença da série com choque pra série sem choque
end


In [18]:
plot(L[:,1], label="y");
plot!(anspirits, label="animal spirits")


<!DOCTYPE html>
 
 
 Plots.jl

In [19]:
plot(L[:,2], label="y com choque")

<!DOCTYPE html>
 
 
 Plots.jl

In [385]:
plot(p, label="p");
plot!(r, label="r")

<!DOCTYPE html>
 
 
 Plots.jl

In [20]:
using Statistics
IRF=mean(M, dims = 2)
plot(IRF, label="Impulso resposta");
plot!(IRF+2*std(M, dims=2), label ="+2 std");
plot!(IRF-2*std(M, dims=2), label ="-2 std")

<!DOCTYPE html>
 
 
 Plots.jl

In [21]:
histogram(L[:,1])

<!DOCTYPE html>
 
 
 Plots.jl

In [22]:
histogram(L[:,2])

<!DOCTYPE html>
 
 
 Plots.jl